In [ ]:
from src.evaluation import QAEvaluator
from dotenv import load_dotenv
import pandas as pd
import os

load_dotenv()

qa_df = pd.read_csv("generated_qa.csv")

qa_df.head()

Загружено 167 записей


message_id                                      original_text  \
0      130738  Итальянский суд принял решение экстрадировать ...   
1      129361  Пять пассажиров автобуса №793 пострадали в ДТП...   
2      133468  Владимир Путин утвердил концепцию государствен...   
3      123139  Генпрокуратура и Минюст подали в Верховный суд...   
4      129894  Обломки дрона обнаружили польские пограничники...   

                                     strict_question  \
0  Какое решение приняло итальянское судопроизвод...   
1  Сколько пассажиров автобуса №793 пострадали в ...   
2  Кто утвердил концепцию государственной миграци...   
3  Какое юридическое действие предприняли Генерал...   
4  Где и кем был обнаружен непилотируемый летател...   

                                       real_question  
0  Что там с Кузнецовым — его в Германию выдадут ...  
1  Сколько человек в автобусе 793 пострадали, ког...  
2  Кто там утвердил новую миграционную концепцию ...  
3  Что Генпрокуратура и Минюст сделали с сатанист...  
4  Что там польские пограничники нашли рядом с Бе...

In [ ]:
evaluator = QAEvaluator(
    df=qa_df,
    text_column="original_text",
    temperature=0.0,
    api_key=os.getenv("OPENROUTER_API_KEY")
)


In [ ]:
batch_size = 5
question_iterator = evaluator.get_questions(
    question_column="strict_question",  # или "real_question"
    batch_size=batch_size
)

print(f"Всего батчей: {len(question_iterator)}")

Всего батчей: 34


## Демонстрация оценки ответов

Ниже показан пример оценки ответов от RAG системы.


In [ ]:
N_DEMO = 5

evaluator_demo = QAEvaluator(
    df=qa_df.head(N_DEMO),
    text_column="original_text",
    api_key=os.getenv("OPENROUTER_API_KEY")
)

question_iterator = evaluator_demo.get_questions(
    question_column="strict_question",
    batch_size=N_DEMO
)

demo_questions = next(iter(question_iterator))

demo_answers = qa_df["original_text"].head(N_DEMO).tolist()

print(f"Демо-вопросов: {len(demo_questions)}")
print(f"Демо-ответов: {len(demo_answers)}")

Демо-вопросов: 5
Демо-ответов: 5


In [ ]:
_ = evaluator_demo.get_questions(
    question_column="strict_question",
    batch_size=N_DEMO
)

metrics = evaluator_demo.evaluate_answers(demo_answers, show_progress=True)

Оценка ответов: 100%|██████████| 5/5 [00:05<00:00,  1.07s/it]


In [13]:
demo_answers

['Итальянский суд принял решение экстрадировать в Германию задержанного по подозрению в подрыве «Северных потоков» Сергея Кузнецова, пишет Reuters.\n\n🐚 Следить за новостями РБК в Telegram',
 'Пять пассажиров автобуса №793 пострадали в ДТП с участием автомобиля, которое произошло на пересечении Мичуринского проспекта и проезда Олимпийской Деревни в Москве, сообщил «Мосгортранс». \n\nПо предварительной информации, водитель автомобиля внезапно перестроился в полосу движения автобуса, из-за чего произошло столкновение. Всем пострадавшим оказывается медицинская помощь.\n\n🐚  Другие видео этого дня — в телеграм-канале РБК',
 'Владимир Путин утвердил концепцию государственной миграционной политики России на 2026-2030 годы.\n\nРезультатом политики должно стать снижение числа нелегальных мигрантов и преступлений.\n\n🐚 Следить за новостями РБК в Telegram',
 'Генпрокуратура и Минюст подали в Верховный суд иск с требованием признать экстремистской организацией «Международное движение сатанизма» и

In [12]:
metrics

{'total_questions': 5,
 'valid_answers': 4,
 'invalid_answers': 1,
 'accuracy': 0.8,
 'avg_relevance': 0.9,
 'avg_completeness': 0.9,
 'avg_factual_accuracy': 1.0,
 'combined_score': 0.9333333333333332,
 'detailed_results': [{'index': 0,
   'question': 'Какое решение приняло итальянское судопроизводство в отношении экстрадиции Сергея Кузнецова в связи с подозрениями в причастности к подрыву газопроводов «Северные потоки»?',
   'answer': 'Итальянский суд принял решение экстрадировать в Германию задержанного по подозрению в подрыве «Северных потоков» Сергея Кузнецова, пишет Reuters.\n\n🐚 Следить за новостями РБК в Telegram',
   'is_valid': True,
   'relevance_score': 1.0,
   'completeness_score': 1.0,
   'factual_accuracy_score': 1.0},
  {'index': 1,
   'question': 'Сколько пассажиров автобуса №793 пострадали в дорожно-транспортном происшествии на пересечении Мичуринского проспекта и проезда Олимпийской Деревни в Москве, вызванном внезапным перестроением автомобиля?',
   'answer': 'Пять 

In [ ]:
results_df = evaluator_demo.get_detailed_results_df(metrics)
results_df

index                                           question  \
0      0  Какое решение приняло итальянское судопроизвод...   
1      1  Сколько пассажиров автобуса №793 пострадали в ...   
2      2  Кто утвердил концепцию государственной миграци...   
3      3  Какое юридическое действие предприняли Генерал...   
4      4  Где и кем был обнаружен непилотируемый летател...   

                                              answer  is_valid  \
0  Итальянский суд принял решение экстрадировать ...      True   
1  Пять пассажиров автобуса №793 пострадали в ДТП...      True   
2  Владимир Путин утвердил концепцию государствен...      True   
3  Генпрокуратура и Минюст подали в Верховный суд...     False   
4  Обломки дрона обнаружили польские пограничники...      True   

   relevance_score  completeness_score  factual_accuracy_score  
0              1.0                 1.0                     1.0  
1              1.0                 1.0                     1.0  
2              1.0                 1.0                     1.0  
3              0.5                 0.5                     1.0  
4              1.0                 1.0                     1.0